##   Code for running 3DVAR with the Lorenz 63 model.
#### Code developed by Greg Hakim, Ryan Torn, Aneesh Subramanian.

In [4]:
import numpy as np
import time
from numpy.linalg import inv
import netCDF4 as nc
import matplotlib as mpl
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
import os
import lorenz63_model as lor

## Wrapping up 3DVar Into Function

In [96]:

def run_3Dvar(assim_len = 1.0, fcst_len = 2.0, nassim = 200, alpha = 4.e-3, H = np.array([[1., 0., 0.], [0., 1., 0.], [0., 0., 1.]]), R = None, verbose = True, super_verbose = False):
    #########################
    # Experiment Parameters #
    #########################
    # assim_len - Time between observations
    # fcst_len  - Forecast length
    # nassim - Number of assimilation times
    # alpha - Alpha control (how fast you try to converge to analysis)

    # H - observation operator
    # H = np.array([[1., 0., 0. ]])  #  observation operator for single observation
    
    nobs = len(H[:,0])
    
    if (R is None):
        R = np.eye(nobs) * 1.0e-2 # - observation error as a diagonal matrix
    # R = np.array([[1.0e-2]])  #  observation error for single observation
    

    np.random.seed(0)

    bfile = nc.Dataset('L63_B.nc')
    invB = inv(bfile.variables['B_matrix'][:,:])
    invR = inv(R)


    ###########################
    # Initialize Empty Arrays #
    ###########################
    xb = np.empty(3)
    xf = np.empty(3)
    xe = np.empty(3)

    yobs  = np.empty(nobs)
    innov = np.empty(nobs)

    xaerr = np.empty((nassim, 3))
    xberr = np.empty((nassim, 3))
    xferr = np.empty((nassim, 3))

    Jfin = np.empty(nassim)


    #############################
    # IC Truth from last column #
    #############################
    xt = np.array(lor.advance(10., 20., 30., 100.))
    ## Runs for 100 time units for 100/0.001 steps, starting at x = 10, y =20, z = 30
    ## Only returns final state


    ############################################
    # Populate Initial State with random error #
    ############################################
    xa = np.empty(3)
    xa = xt[:] + np.random.normal(0, 0.1, 3)
    
    
    #######################################
    # Main Looping Function to Assimilate #
    #######################################
    time1 = time.time()
    niter_track = []
    J_track = []
    intermediate_dist = []
    for t in range(nassim):

        #  Advance analysis to next assimilation time
        xb[0], xb[1], xb[2] = lor.advance(xa[0], xa[1], xa[2], assim_len)

        #  Advance the truth, compute observations at the next time
        xt[0], xt[1], xt[2] = lor.advance(xt[0], xt[1], xt[2], assim_len)
        yobs[:] = np.matmul(H,xt) + np.random.normal(0, np.diag(np.sqrt(R)), nobs)

        xa[:] = xb[:]
        niters = 0
        maxiter = 100
        Jold = 1.0e6
        J = 0.
        J_track_temp = []
        intermediate_dist_temp = []
        
        ## Converging towards a state vector with the least cost function
        while abs(Jold - J) > 1.0e-5:

            Jold = J

            #  Compute innovation, background and observation cost function
            innov[:] = yobs[:] - np.matmul(H,xa)
            Jb = 2.0 * np.matmul(np.matmul(np.transpose(xa - xb), invB), xa - xb)
            J0 = 2.0 * np.matmul(np.matmul(np.transpose(innov), invR), innov)
            J = Jb + J0
            if super_verbose:
                print('   cost function = ',J,", Analysis Error:",np.sqrt(np.sum((xa[:]-xt[:])**2)), "Background Error:",np.sqrt(np.sum((xa[:]-xb[:])**2)),"Jb:",Jb, "J0:",J0)
                
            J_track_temp.append(J)
            intermediate_dist_temp.append((np.sum((xa[:]-xt[:])**2)))

            #  Compute the gradient in the cost function
            gJ = 2.0 * np.matmul(invB,xa - xb) - 2.0 * np.matmul(np.matmul(np.transpose(H),invR),innov)

            #  Compute the new state vector based on cost function gradient
            if niters == 0:
                xa[:] = xa[:] - alpha*gJ[:]
                cgJo = gJ[:]
            else:
                beta = np.matmul(np.transpose(gJ),gJ) / np.matmul(np.transpose(gJo),gJo)
                cgJ = gJ[:] + beta*cgJo[:]
                xa[:] = xa[:] - alpha*cgJ[:]
                cgJo = cgJ[:]

            gJo = gJ[:]

            niters = niters + 1

        if super_verbose:
            print('final cost = ', J, ' after ', niters, ' iterations')
        niter_track.append(niters)
        J_track.append(J_track_temp)
        intermediate_dist.append(intermediate_dist_temp)

        Jfin[t] = J

        #  Compute analysis and background forecast error
        xberr[t,:] = xb[:] - xt[:]
        xaerr[t,:] = xa[:] - xt[:]

        # compute forecast and error
        xf[0], xf[1], xf[2] = lor.advance(xa[0], xa[1], xa[2], fcst_len)
        xe[0], xe[1], xe[2] = lor.advance(xt[0], xt[1], xt[2], fcst_len)
        xferr[t,:] = xf[:] - xe[:]
        
        
    if verbose:
        print('Analysis Error: ',np.sqrt(sum(sum(xaerr[:,:] * xaerr[:,:])) / float(nassim*3)))
        print('Background Error: ',np.sqrt(sum(sum(xberr[:,:] * xberr[:,:])) / float(nassim*3)))
        print('Forecast Error: ',np.sqrt(sum(sum(xferr[:,:] * xferr[:,:])) / float(nassim*3)))

        time2 = time.time()

        print("Total Time:",time2-time1)
        print("Average Iterations to Converge:", np.mean(niter_track))
    
    return (J_track, intermediate_dist, xaerr, xberr, xferr)

## Question 1 ##

In [ ]:
J_track, intermediate_dist, xaerr, xberr, xferr = run_3Dvar()

In [29]:
max_len = max(len(sublist) for sublist in J_track)
J_track_pad = np.array([sublist + [np.nan] * (max_len - len(sublist)) for sublist in J_track])
intermediate_pad = np.array([sublist + [np.nan] * (max_len - len(sublist)) for sublist in intermediate_dist])

In [ ]:
avg_cost_iter = np.nanmean(J_track_pad, axis=0)
for iter, element in enumerate(avg_cost_iter):
    print("Iteration:", iter+1, f"| Average Cost: {element:.4f}")

outliers = J_track_pad[~np.any(np.isnan(J_track_pad), axis=1)]
print("\nOutliers: ", outliers)    


In [ ]:
avg_dist_iter = np.nanmean(intermediate_pad, axis=0)
for iter, element in enumerate(avg_dist_iter):
    print("Iteration:", iter+1, f"| Average Distance: {element:.4f}")

In [ ]:
intermediate_dist
for elem in intermediate_dist:
    domain = [i+1 for i in range(len(elem))]
    plt.plot(domain, elem, marker = 'o',markersize=4,alpha = 0.5)
plt.xlabel("Number of Iterations")
plt.ylabel("Cost Function Value")
plt.title("Intermediate State Distance from the Truth")


## Question 2

In [ ]:
J_track, intermediate_dist, xaerr, xberr, xferr = run_3Dvar(alpha=4.e-3)

In [ ]:
J_track, intermediate_dist, xaerr, xberr, xferr = run_3Dvar(alpha=2.e-3)

In [ ]:
J_track, intermediate_dist, xaerr, xberr, xferr = run_3Dvar(alpha=8.e-3)

## Question 3

In [ ]:
R = np.eye(3)*0.5*10**(-2)
J_track, intermediate_dist, xaerr, xberr, xferr = run_3Dvar(R = R)

In [ ]:
J_track, intermediate_dist, xaerr, xberr, xferr = run_3Dvar(R = np.eye(3) * 4e-2)

In [ ]:
max_len = max(len(sublist) for sublist in J_track)
J_track_pad = np.array([sublist + [np.nan] * (max_len - len(sublist)) for sublist in J_track])
intermediate_pad = np.array([sublist + [np.nan] * (max_len - len(sublist)) for sublist in intermediate_dist])

avg_dist_iter = np.nanmean(intermediate_pad, axis=0)
for iter, element in enumerate(avg_dist_iter):
    print("Iteration:", iter+1, f"| Average Distance: {element:.4f}")

## Question 4

In [92]:
J_track, intermediate_dist, xaerr, xberr, xferr = run_3Dvar(H = np.array([[1., 0., 0.], [0., 0., 0.], [0., 0., 0]]))

   cost function =  20.384179260155026 , Analysis Error: 0.33508046827723703 Background Error: 0.0 Jb: 0.0 J0: 20.384179260155026
   cost function =  9.350800904979957 , Analysis Error: 0.3782275691813034 Background Error: 0.19182066172770895 Jb: 0.005171524521809836 J0: 9.345629380458147
   cost function =  8.894483368293693 , Analysis Error: 0.4016105758874338 Background Error: 0.23770675491158952 Jb: 0.007937342053337104 J0: 8.886546026240357
   cost function =  8.893773671042885 , Analysis Error: 0.40244072782899637 Background Error: 0.23930141191113197 Jb: 0.008038841095507853 J0: 8.885734829947378
   cost function =  8.89374936254998 , Analysis Error: 0.40254858606068855 Background Error: 0.23959526035256548 Jb: 0.008053026506084818 J0: 8.885696336043896
   cost function =  8.893743425773838 , Analysis Error: 0.4025169891397527 Background Error: 0.2396507314843947 Jb: 0.008050475886265767 J0: 8.885692949887572
final cost =  8.893743425773838  after  6  iterations
   cost function

In [ ]:
J_track, intermediate_dist, xaerr, xberr, xferr = run_3Dvar(H = np.array([[0., 0., 0.], [0., 1., 0.], [0., 0., 0]]))

In [95]:
J_track, intermediate_dist, xaerr, xberr, xferr = run_3Dvar(H = np.array([[0., 0., 0.], [0., 0., 0.], [0., 0., 1]]))

   cost function =  22.476733785999375 , Analysis Error: 0.33508046827723703 Background Error: 0.0 Jb: 0.0 J0: 22.476733785999375
   cost function =  17.237540048400636 , Analysis Error: 0.245458188337812 Background Error: 0.13215728123594062 Jb: 0.0004703575040069843 J0: 17.23706969089663
   cost function =  17.01983332490495 , Analysis Error: 0.23014006823846211 Background Error: 0.16385509945462157 Jb: 0.0007230457324419028 J0: 17.01911027917251
   cost function =  17.019494271870787 , Analysis Error: 0.2296661773492501 Background Error: 0.1649612576099665 Jb: 0.000732840916414962 J0: 17.01876143095437
   cost function =  17.01948522573753 , Analysis Error: 0.22958132312775892 Background Error: 0.16516062541238732 Jb: 0.0007346132803816978 J0: 17.018750612457147
final cost =  17.01948522573753  after  5  iterations
   cost function =  564.31254601197 , Analysis Error: 1.9514151878355845 Background Error: 0.0 Jb: 0.0 J0: 564.31254601197
   cost function =  24.398081428077955 , Analys

## Question 5

In [103]:
H = np.array([[1,1,1],[0,0,0],[0,0,0]])
vec = [1,10,100]
J_track, intermediate_dist, xaerr, xberr, xferr = run_3Dvar(H=H)

/var/folders/2d/t7gy2rhs3fn_fgvstmnfq9480000gn/T/ipykernel_20533/1992787286.py:90: RuntimeWarning: overflow encountered in matmul
  Jb = 2.0 * np.matmul(np.matmul(np.transpose(xa - xb), invB), xa - xb)
/var/folders/2d/t7gy2rhs3fn_fgvstmnfq9480000gn/T/ipykernel_20533/1992787286.py:91: RuntimeWarning: overflow encountered in matmul
  J0 = 2.0 * np.matmul(np.matmul(np.transpose(innov), invR), innov)
/var/folders/2d/t7gy2rhs3fn_fgvstmnfq9480000gn/T/ipykernel_20533/1992787286.py:97: RuntimeWarning: overflow encountered in square
  intermediate_dist_temp.append((np.sum((xa[:]-xt[:])**2)))
/var/folders/2d/t7gy2rhs3fn_fgvstmnfq9480000gn/T/ipykernel_20533/1992787286.py:107: RuntimeWarning: overflow encountered in matmul
  beta = np.matmul(np.transpose(gJ),gJ) / np.matmul(np.transpose(gJo),gJo)
/var/folders/2d/t7gy2rhs3fn_fgvstmnfq9480000gn/T/ipykernel_20533/1992787286.py:84: RuntimeWarning: invalid value encountered in scalar subtract
  while abs(Jold - J) > 1.0e-5:
/Users/aidanjanney/VS Code/A

Analysis Error:  nan
Background Error:  nan
Forecast Error:  nan
Total Time: 4.345312833786011
Average Iterations to Converge: 1.075


/var/folders/2d/t7gy2rhs3fn_fgvstmnfq9480000gn/T/ipykernel_20533/1992787286.py:135: RuntimeWarning: overflow encountered in multiply
  print('Analysis Error: ',np.sqrt(sum(sum(xaerr[:,:] * xaerr[:,:])) / float(nassim*3)))


In [104]:
H = np.array([[1,1,1],[0,0,0],[0,0,0]])
vec = [1,10,100]
J_track, intermediate_dist, xaerr, xberr, xferr = run_3Dvar(H=H)

/var/folders/2d/t7gy2rhs3fn_fgvstmnfq9480000gn/T/ipykernel_20533/1992787286.py:90: RuntimeWarning: overflow encountered in matmul
  Jb = 2.0 * np.matmul(np.matmul(np.transpose(xa - xb), invB), xa - xb)
/var/folders/2d/t7gy2rhs3fn_fgvstmnfq9480000gn/T/ipykernel_20533/1992787286.py:91: RuntimeWarning: overflow encountered in matmul
  J0 = 2.0 * np.matmul(np.matmul(np.transpose(innov), invR), innov)
/var/folders/2d/t7gy2rhs3fn_fgvstmnfq9480000gn/T/ipykernel_20533/1992787286.py:97: RuntimeWarning: overflow encountered in square
  intermediate_dist_temp.append((np.sum((xa[:]-xt[:])**2)))
/var/folders/2d/t7gy2rhs3fn_fgvstmnfq9480000gn/T/ipykernel_20533/1992787286.py:107: RuntimeWarning: overflow encountered in matmul
  beta = np.matmul(np.transpose(gJ),gJ) / np.matmul(np.transpose(gJo),gJo)
/var/folders/2d/t7gy2rhs3fn_fgvstmnfq9480000gn/T/ipykernel_20533/1992787286.py:84: RuntimeWarning: invalid value encountered in scalar subtract
  while abs(Jold - J) > 1.0e-5:


Analysis Error:  nan
Background Error:  nan
Forecast Error:  nan
Total Time: 4.40814208984375
Average Iterations to Converge: 1.075


/var/folders/2d/t7gy2rhs3fn_fgvstmnfq9480000gn/T/ipykernel_20533/1992787286.py:135: RuntimeWarning: overflow encountered in multiply
  print('Analysis Error: ',np.sqrt(sum(sum(xaerr[:,:] * xaerr[:,:])) / float(nassim*3)))


In [106]:
H = np.array([[1,1,1],[1,1,1],[1,1,1]])
vec = [1,10,100]
J_track, intermediate_dist, xaerr, xberr, xferr = run_3Dvar(H=H)

/var/folders/2d/t7gy2rhs3fn_fgvstmnfq9480000gn/T/ipykernel_20533/1992787286.py:90: RuntimeWarning: overflow encountered in matmul
  Jb = 2.0 * np.matmul(np.matmul(np.transpose(xa - xb), invB), xa - xb)
/var/folders/2d/t7gy2rhs3fn_fgvstmnfq9480000gn/T/ipykernel_20533/1992787286.py:91: RuntimeWarning: overflow encountered in matmul
  J0 = 2.0 * np.matmul(np.matmul(np.transpose(innov), invR), innov)
/var/folders/2d/t7gy2rhs3fn_fgvstmnfq9480000gn/T/ipykernel_20533/1992787286.py:97: RuntimeWarning: overflow encountered in square
  intermediate_dist_temp.append((np.sum((xa[:]-xt[:])**2)))
/var/folders/2d/t7gy2rhs3fn_fgvstmnfq9480000gn/T/ipykernel_20533/1992787286.py:107: RuntimeWarning: overflow encountered in matmul
  beta = np.matmul(np.transpose(gJ),gJ) / np.matmul(np.transpose(gJo),gJo)
/var/folders/2d/t7gy2rhs3fn_fgvstmnfq9480000gn/T/ipykernel_20533/1992787286.py:84: RuntimeWarning: invalid value encountered in scalar subtract
  while abs(Jold - J) > 1.0e-5:
/Users/aidanjanney/VS Code/A

Analysis Error:  nan
Background Error:  nan
Forecast Error:  nan
Total Time: 4.454912900924683
Average Iterations to Converge: 1.045


/var/folders/2d/t7gy2rhs3fn_fgvstmnfq9480000gn/T/ipykernel_20533/1992787286.py:135: RuntimeWarning: overflow encountered in multiply
  print('Analysis Error: ',np.sqrt(sum(sum(xaerr[:,:] * xaerr[:,:])) / float(nassim*3)))


In [107]:
H = np.array([[1,1,0],[0,0,0],[0,0,0]])
vec = [1,10,100]
J_track, intermediate_dist, xaerr, xberr, xferr = run_3Dvar(H=H)

Analysis Error:  6.030542313670104
Background Error:  9.012724527573315
Forecast Error:  11.09608979689817
Total Time: 8.570574045181274
Average Iterations to Converge: 108.785


In [112]:
H = np.array([[1,-1,0],[0,0,0],[0,0,0]])
vec = [1,10,100]
J_track, intermediate_dist, xaerr, xberr, xferr = run_3Dvar(H=H)

Analysis Error:  10.483098858737868
Background Error:  10.779495826100279
Forecast Error:  10.517627394867446
Total Time: 15.915289163589478
Average Iterations to Converge: 306.24
